In [3]:
!pip install pyarrow fastparquet

from splink import splink_datasets

df = splink_datasets.historical_50k


[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


   ---------------------------------------- 0.0/25.2 MB ? eta -:--:--
   ---------------------------------------- 0.2/25.2 MB 5.6 MB/s eta 0:00:05
    --------------------------------------- 0.3/25.2 MB 3.6 MB/s eta 0:00:07
    --------------------------------------- 0.4/25.2 MB 2.3 MB/s eta 0:00:11
   - -------------------------------------- 0.6/25.2 MB 3.1 MB/s eta 0:00:08
   - -------------------------------------- 0.9/25.2 MB 3.5 MB/s eta 0:00:07
   - -------------------------------------- 1.1/25.2 MB 3.7 MB/s eta 0:00:07
   -- ------------------------------------- 1.4/25.2 MB 4.2 MB/s eta 0:00:06
   -- ------------------------------------- 1.6/25.2 MB 4.2 MB/s eta 0:00:06
   -- ------------------------------------- 1.8/25.2 MB 4.2 MB/s eta 0:00:06
   --- ------------------------------------ 2.0/25.2 MB 4.3 MB/s eta 0:00:06
   --- ------------------------------------ 2.3/25.2 MB 4.5 MB/s eta 0:00:06
   ---- ----------------------------------- 2.6/25.2 MB 4.7 MB/s eta 0:00:05
   ---

In [4]:
df.head()

unique_id   cluster                                         full_name  \
0  Q2296770-1  Q2296770  thomas clifford, 1st baron clifford of chudleigh   
1  Q2296770-2  Q2296770                               thomas of chudleigh   
2  Q2296770-3  Q2296770               tom 1st baron clifford of chudleigh   
3  Q2296770-4  Q2296770                              thomas 1st chudleigh   
4  Q2296770-5  Q2296770              thomas clifford, 1st baron chudleigh   

  first_and_surname first_name    surname         dob birth_place  \
0  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
1  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
2     tom chudleigh        tom  chudleigh  1630-08-01       devon   
3  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   
4  thomas chudleigh     thomas  chudleigh  1630-08-01       devon   

  postcode_fake gender  occupation  
0      tq13 8df   male  politician  
1      tq13 8df   male  politician  
2      tq13 8df   male  politician  
3      tq13 8hu   None  politician  
4      tq13 8df   None  politician

In [5]:
from splink import DuckDBAPI
from splink.exploratory import profile_columns

db_api = DuckDBAPI()
profile_columns(df, db_api, column_expressions=["first_name", "substr(surname,1,2)"])

alt.VConcatChart(...)

In [6]:
from splink import DuckDBAPI, block_on
from splink.blocking_analysis import (
    cumulative_comparisons_to_be_scored_from_blocking_rules_chart,
)

blocking_rules = [
    block_on("substr(first_name,1,3)", "substr(surname,1,4)"),
    block_on("surname", "dob"),
    block_on("first_name", "dob"),
    block_on("postcode_fake", "first_name"),
    block_on("postcode_fake", "surname"),
    block_on("dob", "birth_place"),
    block_on("substr(postcode_fake,1,3)", "dob"),
    block_on("substr(postcode_fake,1,3)", "first_name"),
    block_on("substr(postcode_fake,1,3)", "surname"),
    block_on("substr(first_name,1,2)", "substr(surname,1,2)", "substr(dob,1,4)"),
]

db_api = DuckDBAPI()

cumulative_comparisons_to_be_scored_from_blocking_rules_chart(
    table_or_tables=df,
    blocking_rules=blocking_rules,
    db_api=db_api,
    link_type="dedupe_only",
)

alt.Chart(...)

In [7]:
import splink.comparison_library as cl

from splink import Linker, SettingsCreator

settings = SettingsCreator(
    link_type="dedupe_only",
    blocking_rules_to_generate_predictions=blocking_rules,
    comparisons=[
        cl.ForenameSurnameComparison(
            "first_name",
            "surname",
            forename_surname_concat_col_name="first_name_surname_concat",
        ),
        cl.DateOfBirthComparison(
            "dob", input_is_string=True
        ),
        cl.PostcodeComparison("postcode_fake"),
        cl.ExactMatch("birth_place").configure(term_frequency_adjustments=True),
        cl.ExactMatch("occupation").configure(term_frequency_adjustments=True),
    ],
    retain_intermediate_calculation_columns=True,
)
# Needed to apply term frequencies to first+surname comparison
df["first_name_surname_concat"] = df["first_name"] + " " + df["surname"]
linker = Linker(df, settings, db_api=db_api)

In [8]:
linker.training.estimate_probability_two_random_records_match(
    [
        "l.first_name = r.first_name and l.surname = r.surname and l.dob = r.dob",
        "substr(l.first_name,1,2) = substr(r.first_name,1,2) and l.surname = r.surname and substr(l.postcode_fake,1,2) = substr(r.postcode_fake,1,2)",
        "l.dob = r.dob and l.postcode_fake = r.postcode_fake",
    ],
    recall=0.6,
)

Probability two random records match is estimated to be  0.000136.
This means that amongst all possible pairwise record comparisons, one in 7,362.31 are expected to match.  With 1,279,041,753 total possible comparisons, we expect a total of around 173,728.33 matching pairs


In [9]:
linker.training.estimate_u_using_random_sampling(max_pairs=5e6)

----- Estimating u probabilities using random sampling -----


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

u probability not trained for first_name_surname - Match on reversed cols: first_name and surname (both directions) (comparison vector value: 5). This usually means the comparison level was never observed in the training data.

Estimated u probabilities using random sampling

Your model is not yet fully trained. Missing estimates for:
    - first_name_surname (some u values are not trained, no m values are trained).
    - dob (no m values are trained).
    - postcode_fake (no m values are trained).
    - birth_place (no m values are trained).
    - occupation (no m values are trained).


In [10]:
training_blocking_rule = block_on("first_name", "surname")
training_session_names = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
(l."first_name" = r."first_name") AND (l."surname" = r."surname")

Parameter estimates will be made for the following comparison(s):
    - dob
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - first_name_surname

Iteration 1: Largest change in params was 0.248 in probability_two_random_records_match
Iteration 2: Largest change in params was -0.0931 in the m_probability of postcode_fake, level `Exact match on full postcode`
Iteration 3: Largest change in params was -0.0231 in the m_probability of birth_place, level `Exact match on birth_place`
Iteration 4: Largest change in params was 0.00912 in the m_probability of birth_place, level `All other comparisons`
Iteration 5: Largest change in params was 0.00413 in the m_probability of birth_place, level `All other comp

In [11]:
training_blocking_rule = block_on("dob")
training_session_dob = (
    linker.training.estimate_parameters_using_expectation_maximisation(
        training_blocking_rule, estimate_without_term_frequencies=True
    )
)


----- Starting EM training session -----

Estimating the m probabilities of the model by blocking on:
l."dob" = r."dob"

Parameter estimates will be made for the following comparison(s):
    - first_name_surname
    - postcode_fake
    - birth_place
    - occupation

Parameter estimates cannot be made for the following comparison(s) since they are used in the blocking rules: 
    - dob


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))


Iteration 1: Largest change in params was -0.472 in the m_probability of first_name_surname, level `Exact match on first_name_surname_concat`
Iteration 2: Largest change in params was 0.0522 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 3: Largest change in params was 0.0175 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 4: Largest change in params was 0.00533 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 5: Largest change in params was 0.00163 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 6: Largest change in params was 0.000509 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 7: Largest change in params was 0.00016 in the m_probability of first_name_surname, level `All other comparisons`
Iteration 8: Largest change in params was 5.06e-05 in the m_probability of first_name_surname, level `All other co

In [12]:
linker.visualisations.match_weights_chart()

alt.VConcatChart(...)

In [13]:
linker.evaluation.unlinkables_chart()

alt.LayerChart(...)

In [14]:
df_predict = linker.inference.predict()
df_e = df_predict.as_pandas_dataframe(limit=5)
df_e

Blocking time: 1.81 seconds


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Predict time: 3.16 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


match_weight  match_probability   unique_id_l  unique_id_r first_name_l  \
0     16.261321           0.999987  Q15889913-13  Q15889913-2           ed   
1     -0.816225           0.362215   Q6225175-10   Q6225175-3        jonas   
2     21.821249           1.000000   Q6238935-10   Q6238935-4         john   
3     25.415544           1.000000   Q6238935-16   Q6238935-4         john   
4     19.881703           0.999999   Q3806593-10   Q3806593-4        kames   

  first_name_r surname_l surname_r first_name_surname_concat_l  \
0       edward   simpson   simpson                  ed simpson   
1         john    carlin    carlin                jonas carlin   
2           h.  robinson  robinson               john robinson   
3           h.  robinson  robinson               john robinson   
4        james  hamilton  hamilton              kames hamilton   

  first_name_surname_concat_r  ...  bf_birth_place  bf_tf_adj_birth_place  \
0              edward simpson  ...        0.162120               1.000000   
1                 john carlin  ...        0.162120               1.000000   
2                 h. robinson  ...      146.131904               2.505609   
3                 h. robinson  ...      146.131904               2.505609   
4              james hamilton  ...      146.131904               4.320016   

                  occupation_l                 occupation_r  gamma_occupation  \
0                archaeologist                archaeologist                 1   
1                    cricketer               cricket umpire                 0   
2                       drawer                       drawer                 1   
3                       drawer                       drawer                 1   
4  association football player  association football player                 1   

   tf_occupation_l  tf_occupation_r  bf_occupation  bf_tf_adj_occupation  \
0         0.002214         0.002214      21.197361             19.106243   
1         0.121001         0.001859       0.107721              1.000000   
2         0.003836         0.003836      21.197361             11.030408   
3         0.003836         0.003836      21.197361             11.030408   
4         0.027443         0.027443      21.197361              1.541714   

  match_key  
0         4  
1         4  
2         4  
3         4  
4         4  

[5 rows x 42 columns]

In [15]:
records_to_plot = df_e.to_dict(orient="records")
linker.visualisations.waterfall_chart(records_to_plot, filter_nulls=False)

alt.LayerChart(...)

In [16]:
clusters = linker.clustering.cluster_pairwise_predictions_at_threshold(
    df_predict, threshold_match_probability=0.95
)

Completed iteration 1, num representatives needing updating: 842
Completed iteration 2, num representatives needing updating: 184
Completed iteration 3, num representatives needing updating: 60
Completed iteration 4, num representatives needing updating: 6
Completed iteration 5, num representatives needing updating: 1
Completed iteration 6, num representatives needing updating: 0


In [18]:
from IPython.display import IFrame

linker.visualisations.cluster_studio_dashboard(
    df_predict,
    clusters,
    "50k_cluster.html",
    sampling_method="by_cluster_size",
    overwrite=True,
)


IFrame(src="./50k_cluster.html", width="100%", height=1200)

In [19]:
linker.evaluation.accuracy_analysis_from_labels_column(
    "cluster", output_type="accuracy", match_weight_round_to_nearest=0.02
)

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Blocking time: 2.45 seconds


FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Predict time: 4.13 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)

In [20]:
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.999,
    include_false_negatives=False,
    include_false_positives=True,
).as_record_dict()
linker.visualisations.waterfall_chart(records)

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Blocking time: 2.65 seconds
Predict time: 0.69 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)

In [21]:
# Some of the false negatives will be because they weren't detected by the blocking rules
records = linker.evaluation.prediction_errors_from_labels_column(
    "cluster",
    threshold_match_probability=0.5,
    include_false_negatives=True,
    include_false_positives=False,
).as_record_dict(limit=50)

linker.visualisations.waterfall_chart(records)

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Blocking time: 2.63 seconds
Predict time: 0.62 seconds

 -- WARNING --
You have called predict(), but there are some parameter estimates which have neither been estimated or specified in your settings dictionary.  To produce predictions the following untrained trained parameters will use default values.
Comparison: 'first_name_surname':
    u values not fully trained


alt.LayerChart(...)